# Computation of layer by layer containment corrections




## Setup

In [54]:
import sys
sys.path.insert(0, '..')
sys.path.insert(1, 'python/')

import ROOT
import root_numpy as rnp
import python.l1THistos as histos
import math
import uuid
import pandas as pd

from drawingTools import *

ROOT.enableJSVis()
#ROOT.enableJSVis()

#from drawingTools import *

normalized_histos = list()
    

In [2]:
# %load python/drawingTools.py


In [55]:
# %load samples.py
import ROOT
import pandas as pd


samples = [
    HistoFile('doubleele_flat1to100_PU200_iso', 'PU200', 'v150.68A', 'dele'),
    HistoFile('doublephoton_flat1to100_PU200_iso', 'PU200', 'v150.68A', 'dpho'),
    HistoFile('nugun_alleta_pu200_iso', 'PU200', 'v150.68A', 'mb'),
]


In [56]:
for smp in samples:
    smp.print_primitives()


<HistoFile ../plots1/histos_doubleele_flat1to100_PU200_iso_v150.68A.root, dele>
--- HistoClass: 
['IsoTuples']
--- TPs: 
['tkEmEE', 'PFNFtkEleEE', 'tkEleEE', 'PFNFtkEmEE']
--- TP selections:
{   'PFNFtkEleEE': ['EGq2', 'EGq1'],
    'PFNFtkEmEE': ['EGq2', 'EGq1'],
    'tkEleEE': ['EGq4', 'EGq5'],
    'tkEmEE': ['EGq4', 'EGq5']}
--- GEN selections:
{   'PFNFtkEleEE': ['GENEe'],
    'PFNFtkEmEE': ['GENEe'],
    'tkEleEE': ['GENEe'],
    'tkEmEE': ['GENEe']}
<HistoFile ../plots1/histos_doublephoton_flat1to100_PU200_iso_v150.68A.root, dpho>
--- HistoClass: 
['IsoTuples']
--- TPs: 
['tkEmEE', 'PFNFtkEleEE', 'tkEleEE', 'PFNFtkEmEE']
--- TP selections:
{   'PFNFtkEleEE': ['EGq2', 'EGq1'],
    'PFNFtkEmEE': ['EGq2', 'EGq1'],
    'tkEleEE': ['EGq4', 'EGq5'],
    'tkEmEE': ['EGq4', 'EGq5']}
--- GEN selections:
{   'PFNFtkEleEE': ['GENEe'],
    'PFNFtkEmEE': ['GENEe'],
    'tkEleEE': ['GENEe'],
    'tkEmEE': ['GENEe']}
<HistoFile ../plots1/histos_nugun_alleta_pu200_iso_v150.68A.root, mb>
--- Histo

In [57]:
import python.collections as collections
import python.selections as selections

labels_dict = {}

evm = collections.EventManager()
labels_dict.update(evm.get_labels())
selm = selections.SelectionManager()
labels_dict.update(selm.get_labels())



## Computation of the values

### read the iso trees

In [58]:
import uproot4 as up

import array
import numpy as np 

tree_data = pd.DataFrame()

frames = []
for smp in samples:    
    print ("")
    print ('------ SAMPLE: {}, PU: {}'.format(smp.type, smp.label))
    upfile = up.open(smp.histo_filename, num_workers=2)
    ph = smp.build_file_primitive_index(debug=False)
    tps = ph.tp.unique()
    for tp in tps:
        for gen_sel in ph[ph.tp == tp].gen_sel.unique():
            for tp_sel in ph[(ph.tp == tp) & (ph.gen_sel == gen_sel)].tp_sel.unique():
                print ('TP: {} sel: {}, gen_sel: {}'.format(tp, tp_sel, gen_sel))
                tree_name = 'IsoTuples/{}_{}_{}_iso'.format(tp, tp_sel, gen_sel)
                branches=[
                    'pid_gen',
                    'e_gen',
                    'pt_gen',
                    'eta_gen',
                    'z0_gen',
                    'e',
                    'pt',
                    'eta',
                    'tkIso', 
                    'pfIso', 
                    'tkIsoPV', 
                    'pfIsoPV']

                uptree = upfile[tree_name]
                df = uptree.arrays(
                    branches, 
                    library='pd')
                
                df.loc[:, 'signal'] = 1
                df.loc[df['pid_gen'] == -1, ['signal']] = 0
                df.loc[:, 'smp'] = smp.type
                df.loc[:, 'pu'] = smp.label
                df.loc[:, 'tp'] = tp
                df.loc[:, 'gen_sel'] = gen_sel
                df.loc[:, 'tp_sel'] = tp_sel
#                 frames.append(df)
                tree_data = tree_data.append(df, ignore_index=True)
                del df
# tree_data = pd.concat(frames, ignore_index=True)


------ SAMPLE: dele, PU: PU200
TP: tkEmEE sel: EGq4, gen_sel: GENEe
TP: tkEmEE sel: EGq5, gen_sel: GENEe
TP: PFNFtkEleEE sel: EGq2, gen_sel: GENEe
TP: PFNFtkEleEE sel: EGq1, gen_sel: GENEe
TP: tkEleEE sel: EGq4, gen_sel: GENEe
TP: tkEleEE sel: EGq5, gen_sel: GENEe
TP: PFNFtkEmEE sel: EGq2, gen_sel: GENEe
TP: PFNFtkEmEE sel: EGq1, gen_sel: GENEe

------ SAMPLE: dpho, PU: PU200
TP: tkEmEE sel: EGq4, gen_sel: GENEe
TP: tkEmEE sel: EGq5, gen_sel: GENEe
TP: PFNFtkEleEE sel: EGq2, gen_sel: GENEe
TP: PFNFtkEleEE sel: EGq1, gen_sel: GENEe
TP: tkEleEE sel: EGq4, gen_sel: GENEe
TP: tkEleEE sel: EGq5, gen_sel: GENEe
TP: PFNFtkEmEE sel: EGq2, gen_sel: GENEe
TP: PFNFtkEmEE sel: EGq1, gen_sel: GENEe

------ SAMPLE: mb, PU: PU200
TP: tkEmEE sel: EGq4, gen_sel: GENEe
TP: tkEmEE sel: EGq5, gen_sel: GENEe
TP: PFNFtkEleEE sel: EGq2, gen_sel: GENEe
TP: PFNFtkEleEE sel: EGq1, gen_sel: GENEe
TP: tkEleEE sel: EGq4, gen_sel: GENEe
TP: tkEleEE sel: EGq5, gen_sel: GENEe
TP: PFNFtkEmEE sel: EGq2, gen_sel: GENEe

In [59]:
tree_data.smp.unique()

array(['dele', 'dpho', 'mb'], dtype=object)

In [60]:
tree_data.loc[tree_data['pid_gen'] == -1, ['signal']] = 0

In [61]:
tree_data.iloc[:10]

pid_gen  e_gen  pt_gen  eta_gen  z0_gen          e        pt           eta  \
0     -1.0   -1.0    -1.0     -1.0    -1.0   0.000000  0.000000  45508.878906   
1     -1.0   -1.0    -1.0     -1.0    -1.0   0.000000  0.000000  45508.898438   
2     -1.0   -1.0    -1.0     -1.0    -1.0   0.000000  0.000000  45508.859375   
3     -1.0   -1.0    -1.0     -1.0    -1.0   0.000000  0.000000  45508.871094   
4     -1.0   -1.0    -1.0     -1.0    -1.0   0.000000  0.000000  45508.871094   
5     -1.0   -1.0    -1.0     -1.0    -1.0   0.000000  0.000000  45508.886719   
6     -1.0   -1.0    -1.0     -1.0    -1.0   0.000000  0.000000  45508.871094   
7     -1.0   -1.0    -1.0     -1.0    -1.0   0.487876  0.043684     -3.104220   
8     -1.0   -1.0    -1.0     -1.0    -1.0   8.195891  0.729138     -3.110688   
9     -1.0   -1.0    -1.0     -1.0    -1.0  22.432461  2.102239     -3.058450   

   tkIso  pfIso  tkIsoPV  pfIsoPV  signal   smp     pu      tp gen_sel tp_sel  
0 -999.0 -999.0   -999.0   -999.0       0  dele  PU200  tkEmEE   GENEe   EGq4  
1 -999.0 -999.0   -999.0   -999.0       0  dele  PU200  tkEmEE   GENEe   EGq4  
2 -999.0 -999.0   -999.0   -999.0       0  dele  PU200  tkEmEE   GENEe   EGq4  
3 -999.0 -999.0   -999.0   -999.0       0  dele  PU200  tkEmEE   GENEe   EGq4  
4 -999.0 -999.0   -999.0   -999.0       0  dele  PU200  tkEmEE   GENEe   EGq4  
5 -999.0 -999.0   -999.0   -999.0       0  dele  PU200  tkEmEE   GENEe   EGq4  
6 -999.0 -999.0   -999.0   -999.0       0  dele  PU200  tkEmEE   GENEe   EGq4  
7    0.0 -999.0      0.0   -999.0       0  dele  PU200  tkEmEE   GENEe   EGq4  
8    0.0 -999.0      0.0   -999.0       0  dele  PU200  tkEmEE   GENEe   EGq4  
9    0.0 -999.0      0.0   -999.0       0  dele  PU200  tkEmEE   GENEe   EGq4

In [62]:
tree_data[(tree_data['signal'] == 0) & (tree_data['smp'] == 'mb')].iloc[:10]

pid_gen  e_gen  pt_gen  eta_gen  z0_gen         e        pt  \
39117632     -1.0   -1.0    -1.0     -1.0    -1.0  0.000000  0.000000   
39117633     -1.0   -1.0    -1.0     -1.0    -1.0  0.000000  0.000000   
39117634     -1.0   -1.0    -1.0     -1.0    -1.0  1.089435  0.098639   
39117635     -1.0   -1.0    -1.0     -1.0    -1.0  6.959329  0.639826   
39117636     -1.0   -1.0    -1.0     -1.0    -1.0  0.000000  0.000000   
39117637     -1.0   -1.0    -1.0     -1.0    -1.0  0.000000  0.000000   
39117638     -1.0   -1.0    -1.0     -1.0    -1.0  0.000000  0.000000   
39117639     -1.0   -1.0    -1.0     -1.0    -1.0  0.000000  0.000000   
39117640     -1.0   -1.0    -1.0     -1.0    -1.0  0.000000  0.000000   
39117641     -1.0   -1.0    -1.0     -1.0    -1.0  0.000000  0.000000   

                   eta  tkIso  pfIso  tkIsoPV  pfIsoPV  signal smp     pu  \
39117632  45508.894531 -999.0 -999.0   -999.0   -999.0       0  mb  PU200   
39117633  45508.859375 -999.0 -999.0   -999.0   -999.0       0  mb  PU200   
39117634     -3.093039    0.0 -999.0      0.0   -999.0       0  mb  PU200   
39117635     -3.077669    0.0 -999.0      0.0   -999.0       0  mb  PU200   
39117636  45508.914062 -999.0 -999.0   -999.0   -999.0       0  mb  PU200   
39117637  45508.890625 -999.0 -999.0   -999.0   -999.0       0  mb  PU200   
39117638  45508.843750 -999.0 -999.0   -999.0   -999.0       0  mb  PU200   
39117639  45508.933594 -999.0 -999.0   -999.0   -999.0       0  mb  PU200   
39117640  45508.875000 -999.0 -999.0   -999.0   -999.0       0  mb  PU200   
39117641  45508.894531 -999.0 -999.0   -999.0   -999.0       0  mb  PU200   

              tp gen_sel tp_sel  
39117632  tkEmEE   GENEe   EGq4  
39117633  tkEmEE   GENEe   EGq4  
39117634  tkEmEE   GENEe   EGq4  
39117635  tkEmEE   GENEe   EGq4  
39117636  tkEmEE   GENEe   EGq4  
39117637  tkEmEE   GENEe   EGq4  
39117638  tkEmEE   GENEe   EGq4  
39117639  tkEmEE   GENEe   EGq4  
39117640  tkEmEE   GENEe   EGq4  
39117641  tkEmEE   GENEe   EGq4

In [63]:
sample_sel = {
    'dele': '((smp == "dele") & (pu == "PU200") & (pid_gen != -1)) | ((smp == "mb") & (pid_gen == -1))',
    'dpho': '((smp == "dpho") & (pu == "PU200") & (pid_gen != -1)) | ((smp == "mb") & (pid_gen == -1))'
}



# sample_sel = '((smp == "dele") & (pu == "PU200") & (pid_gen != -1)) | ((smp == "mb") & (pid_gen == -1))'



In [64]:
sig_sel = [
    selections.Selection('all', '', ''),
    selections.Selection('Sig', 'SIG', 'signal == 1'),
    selections.Selection('Bkg', 'BKG', 'signal == 0'),
]

pt_sel = [
    selections.Selection('Pt5', 'p_{T}>5GeV', 'pt>5'),
    selections.Selection('Pt10', 'p_{T}>10GeV', 'pt>10'),
    selections.Selection('Pt20', 'p_{T}>20GeV', 'pt>20'),
#     selections.Selection('Pt25', 'p_{T}>25GeV', 'pt>25'),
    selections.Selection('Pt40', 'p_{T}>40GeV', 'pt>40'),
    selections.Selection('GENPt5', 'p^{GEN}_{T}>5GeV', 'pt_gen>5'),
    selections.Selection('GENPt10', 'p^{GEN}_{T}>10GeV', 'pt_gen>10'),
    selections.Selection('GENPt20', 'p^{GEN}_{T}>20GeV', 'pt_gen>20'),
#     selections.Selection('Pt25', 'p_{T}>25GeV', 'pt>25'),
    selections.Selection('GENPt40', 'p^{GEN}_{T}>40GeV', 'pt_gen>40'),

]

tp_sel = [
    selections.Selection('tkEleEE', 'tkEleEE', '(tp == "tkEleEE") & (tp_sel == "EGq5")'),
    selections.Selection('tkEmEE', 'tkEmEE', '(tp == "tkEmEE") & (tp_sel == "EGq5")'),
    selections.Selection('PFTkEleEE', 'PFTkEleEE', '(tp == "PFNFtkEleEE") & (tp_sel == "EGq2")'),
    selections.Selection('PFTkEmEE', 'PFTkEmEE', '(tp == "PFNFtkEmEE") & (tp_sel == "EGq2")'),
    #     selections.Selection('PFTkEleEE', 'PFTkEleEE', '(tp == "PFNFtkEleEE") & (tp_sel == "EGq5")'),
#     selections.Selection('PFTkEmEE', 'PFTkEmEE', '(tp == "PFNFtkEmEE") & (tp_sel == "EGq5")'),
#     selections.Selection('PFTkEleEB', 'PFTkEleEB', '(tp == "PFNFtkEleEB")'),
#     selections.Selection('PFTkEmEB', 'PFTkEmEB', '(tp == "PFNFtkEmEB")'),

]

eta_sel = [
#     selections.Selection('EtaABC', '|#eta| < 2.4', '(abs(eta) < 2.4)'),
    selections.Selection('EtaBC', '1.52<|#eta| < 2.4', '(abs(eta) < 2.4) & (abs(eta) > 1.52)'),
    selections.Selection('EtaBCp', '1.52< #eta < 2.4', '(eta < 2.4) & (eta > 1.52)'),
    selections.Selection('EtaBCm', '-2.4< #eta < -1.5', '(eta > -2.4) & (eta < -1.52)'),
#     selections.Selection('EtaF', '|#eta| < 1.49', '(abs(eta) < 1.49)'),

]

eta_pt_sel = selections.multiply_selections(eta_sel, pt_sel)

selects = selections.multiply_selections(eta_pt_sel, sig_sel)

In [65]:
for sel in selects:
    print(sel)
labels_dict.update(selm.get_labels())


n: EtaBCPt5, s: ((abs(eta) < 2.4) & (abs(eta) > 1.52)) & (pt>5), l:1.52<|#eta| < 2.4, p_{T}>5GeV
n: EtaBCPt5Sig, s: (((abs(eta) < 2.4) & (abs(eta) > 1.52)) & (pt>5)) & (signal == 1), l:1.52<|#eta| < 2.4, p_{T}>5GeV, SIG
n: EtaBCPt5Bkg, s: (((abs(eta) < 2.4) & (abs(eta) > 1.52)) & (pt>5)) & (signal == 0), l:1.52<|#eta| < 2.4, p_{T}>5GeV, BKG
n: EtaBCPt10, s: ((abs(eta) < 2.4) & (abs(eta) > 1.52)) & (pt>10), l:1.52<|#eta| < 2.4, p_{T}>10GeV
n: EtaBCPt10Sig, s: (((abs(eta) < 2.4) & (abs(eta) > 1.52)) & (pt>10)) & (signal == 1), l:1.52<|#eta| < 2.4, p_{T}>10GeV, SIG
n: EtaBCPt10Bkg, s: (((abs(eta) < 2.4) & (abs(eta) > 1.52)) & (pt>10)) & (signal == 0), l:1.52<|#eta| < 2.4, p_{T}>10GeV, BKG
n: EtaBCPt20, s: ((abs(eta) < 2.4) & (abs(eta) > 1.52)) & (pt>20), l:1.52<|#eta| < 2.4, p_{T}>20GeV
n: EtaBCPt20Sig, s: (((abs(eta) < 2.4) & (abs(eta) > 1.52)) & (pt>20)) & (signal == 1), l:1.52<|#eta| < 2.4, p_{T}>20GeV, SIG
n: EtaBCPt20Bkg, s: (((abs(eta) < 2.4) & (abs(eta) > 1.52)) & (pt>20)) & (signa

In [66]:
from sklearn import metrics

class IsoPlot(histos.BaseHistos):
    def __init__(self, name, root_file=None, debug=False):
        self.h_pt = histo_pt = ROOT.TH1F(name+'_pt', 'pt; p_{T} [GeV]', 100, 0, 100)
        self.h_abseta = ROOT.TH1F(name+'_eta', 'heta; |#eta|', 100, 0, 3.5)
        self.h_tkIso = ROOT.TH1F(name+'_tkIso', 'tk-iso (rel.); tk-iso (rel.)', 100, 0, 2)
        self.h_pfIso = ROOT.TH1F(name+'_pfIso', 'PF-iso (rel.); PF-iso (rel.)', 100, 0, 2)
        self.h_tkIsoPV = ROOT.TH1F(name+'_tkIsoPV', ';tk-iso PV (rel.)', 100, 0, 2)
        self.h_pfIsoPV = ROOT.TH1F(name+'_pfIsoPV', ';PF-iso PV (rel.)', 100, 0, 2)
        self.g_tkIso_roc = None
        self.g_tkIso_effSig = None
        self.g_tkIso_rejBkg = None

        self.g_pfIso_roc = None
        self.g_pfIso_effSig = None
        self.g_pfIso_rejBkg = None

        self.g_tkIsoPV_roc = None
        self.g_tkIsoPV_effSig = None
        self.g_tkIsoPV_rejBkg = None
        
        self.g_pfIsoPV_roc = None
        self.g_pfIsoPV_effSig = None
        self.g_pfIsoPV_rejBkg = None

        histos.BaseHistos.__init__(self, name, root_file)   

    
    def fill_roc(self, score_name, data_flag, data_score):
        fpr, tpr, thresholds = metrics.roc_curve(y_true=data_flag, y_score =data_score)
        g_roc = ROOT.TGraph(len(fpr), fpr, 1-tpr)
        g_roc.SetTitle(f"ROC {score_name}; 1 - bck. eff.; sig. eff.")
        g_eff_sig = ROOT.TGraph(len(thresholds), array.array('d', thresholds), 1-tpr)
        g_eff_sig.SetTitle(f'Eff. {score_name}; {score_name} (rel.); sig. eff.')
        g_eff_sig = ROOT.TGraph(len(thresholds), array.array('d', thresholds), 1-tpr)
        g_eff_sig.SetTitle(f'Eff. {score_name}; {score_name} (rel.); sig. eff.')
        g_rej_bkg = ROOT.TGraph(len(thresholds), array.array('d', thresholds), fpr)
        g_rej_bkg.SetTitle(f'Rej eff. {score_name}; {score_name} (rel.); bkg rej. eff.')

        return g_roc, g_eff_sig, g_rej_bkg
    
    def fill(self, data):
        rnp.fill_hist(self.h_pt, data.pt)
        rnp.fill_hist(self.h_abseta, np.abs(data.eta))
        rnp.fill_hist(self.h_tkIso, data.tkIso)
        rnp.fill_hist(self.h_pfIso, data.pfIso)
        rnp.fill_hist(self.h_tkIsoPV, data.tkIsoPV)
        rnp.fill_hist(self.h_pfIsoPV, data.pfIsoPV)

        self.g_tkIso_roc, self.g_tkIso_effSig, self.g_tkIso_rejBkg = self.fill_roc('tk-iso', data.signal, data.tkIso)
        self.g_pfIso_roc, self.g_pfIso_effSig, self.g_pfIso_rejBkg = self.fill_roc('pf-iso', data.signal, data.pfIso)
        self.g_tkIsoPV_roc, self.g_tkIsoPV_effSig, self.g_tkIsoPV_rejBkg = self.fill_roc('tk-isoPV', data.signal, data.tkIsoPV)
        self.g_pfIsoPV_roc, self.g_pfIsoPV_effSig, self.g_pfIsoPV_rejBkg = self.fill_roc('pf-isoPV', data.signal, data.pfIsoPV)
        
        

In [67]:
class HWrapperLazy(object):
    def __init__(self, histo):
        self.histo = histo
        self.data_df = None
        self.data_sel = None
        self.filled = False
        
    def fill_df(self, data, selection):
        self.data_df = data
        self.data_sel = selection
        
    def get(self, debug=False):
        if not self.filled:
            print('Wrapper: {} not filled!'.format(self))
            self.histo.fill(self.data_df.query(self.data_sel))
            self.filled = True
        return self.histo


In [68]:


hplot_iso = HPlot(samples, labels_dict)


In [69]:
samples_dele = [smp for smp in samples if smp.type == 'dele']
samples_dpho = [smp for smp in samples if smp.type == 'dpho']



In [70]:
%time

for smp in samples_dele+samples_dpho:
    sb_tree = tree_data.query(sample_sel[smp.type])
    for tp in tp_sel:
        for sel in selects:
            tp_and_sel = tp+sel
#             sel_df = sb_tree.query(tp_and_sel.selection)
            h_iso = HWrapperLazy(
                        IsoPlot(name='{}_{}_{}_{}_{}'.format(smp.type, smp.label, tp.name, sel.name, None)))

            h_iso.fill_df(sb_tree, tp_and_sel.selection)
        
            hplot_iso.data = hplot_iso.data.append(
                {'sample': smp.type,
                 'pu': smp.label,
                 'tp': tp.name,
                 'tp_sel': sel.name,
                 'gen_sel': None,
                 'classtype': IsoPlot,
                 'histo': h_iso,},
                ignore_index=True)
   


CPU times: user 4 µs, sys: 1e+03 ns, total: 5 µs
Wall time: 7.15 µs


In [71]:
hplot_iso.data.iloc[:10]

sample     pu       tp        tp_sel gen_sel                   classtype  \
0   dele  PU200  tkEleEE      EtaBCPt5    None  <class '__main__.IsoPlot'>   
1   dele  PU200  tkEleEE   EtaBCPt5Sig    None  <class '__main__.IsoPlot'>   
2   dele  PU200  tkEleEE   EtaBCPt5Bkg    None  <class '__main__.IsoPlot'>   
3   dele  PU200  tkEleEE     EtaBCPt10    None  <class '__main__.IsoPlot'>   
4   dele  PU200  tkEleEE  EtaBCPt10Sig    None  <class '__main__.IsoPlot'>   
5   dele  PU200  tkEleEE  EtaBCPt10Bkg    None  <class '__main__.IsoPlot'>   
6   dele  PU200  tkEleEE     EtaBCPt20    None  <class '__main__.IsoPlot'>   
7   dele  PU200  tkEleEE  EtaBCPt20Sig    None  <class '__main__.IsoPlot'>   
8   dele  PU200  tkEleEE  EtaBCPt20Bkg    None  <class '__main__.IsoPlot'>   
9   dele  PU200  tkEleEE     EtaBCPt40    None  <class '__main__.IsoPlot'>   

                                           histo  
0  <__main__.HWrapperLazy object at 0x14ce87310>  
1  <__main__.HWrapperLazy object at 0x14c8f48e0>  
2  <__main__.HWrapperLazy object at 0x14ce87340>  
3  <__main__.HWrapperLazy object at 0x14dd4fee0>  
4  <__main__.HWrapperLazy object at 0x14dd4fa60>  
5  <__main__.HWrapperLazy object at 0x14dd4f6d0>  
6  <__main__.HWrapperLazy object at 0x14dd4fa30>  
7  <__main__.HWrapperLazy object at 0x14dd4ff10>  
8  <__main__.HWrapperLazy object at 0x14dd4f820>  
9  <__main__.HWrapperLazy object at 0x14c673a30>

In [72]:
hsets, labels, text = hplot_iso.get_histo(IsoPlot, ['dele'], 'PU200', ['PFTkEleEE'], ['EtaBCPt5', 'EtaBCPt10', 'EtaBCPt20'], None)
draw([his.h_pt for his in hsets], labels, text=text,  
#      min_y=1, max_y=40000,
#      min_x=0, max_x=60,
#      logy=True, x_axis_label='online p_{T} thresh. [GeV]'
    )


Wrapper: <__main__.HWrapperLazy object at 0x14c4e8c40> not filled!
Wrapper: <__main__.HWrapperLazy object at 0x14c4dc6a0> not filled!
Wrapper: <__main__.HWrapperLazy object at 0x14c4dc0d0> not filled!


In [73]:
hsets, labels, text = hplot_iso.get_histo(IsoPlot, ['dele'], 'PU200', ['PFTkEleEE', 'tkEleEE'], ['EtaBCPt5Sig'], None)

draw([his.h_tkIso for his in hsets], labels, text=text,  
     min_y=1, max_y=10000,
#      min_x=0, max_x=60,
     logy=True, 
#      x_axis_label='online p_{T} thresh. [GeV]'
    )
draw([his.h_pfIso for his in hsets], labels, text=text,  
      min_y=1, max_y=10000,
#      min_x=0, max_x=60,
     logy=True, 
#      x_axis_label='online p_{T} thresh. [GeV]'
    )


Wrapper: <__main__.HWrapperLazy object at 0x14c4e80d0> not filled!


/Users/cerminar/.virtualenvs/HGCTPGPerformance-py3.8/lib/python3.8/site-packages/sklearn/metrics/_ranking.py:803: UndefinedMetricWarning: No negative samples in y_true, false positive value should be meaningless
  warnings.warn("No negative samples in y_true, "


Wrapper: <__main__.HWrapperLazy object at 0x14c8f48e0> not filled!


/Users/cerminar/.virtualenvs/HGCTPGPerformance-py3.8/lib/python3.8/site-packages/sklearn/metrics/_ranking.py:803: UndefinedMetricWarning: No negative samples in y_true, false positive value should be meaningless
  warnings.warn("No negative samples in y_true, "


In [74]:
hsets, labels, text = hplot_iso.get_histo(IsoPlot, ['dele'], 'PU200', ['tkEmEE'], ['EtaBCPt5Sig', 'EtaBCpPt5Sig', 'EtaBCmPt5Sig'], None)

draw([his.h_tkIso for his in hsets], labels, text=text,  
#      min_y=1, max_y=10000,
#      min_x=0, max_x=60,
     logy=True, 
     norm=True,
#      x_axis_label='online p_{T} thresh. [GeV]'
    )
draw([his.h_pfIso for his in hsets], labels, text=text,  
      min_y=1, max_y=10000,
#      min_x=0, max_x=60,
     logy=True, 
#      x_axis_label='online p_{T} thresh. [GeV]'
    )


Wrapper: <__main__.HWrapperLazy object at 0x14de5db20> not filled!


/Users/cerminar/.virtualenvs/HGCTPGPerformance-py3.8/lib/python3.8/site-packages/sklearn/metrics/_ranking.py:803: UndefinedMetricWarning: No negative samples in y_true, false positive value should be meaningless
  warnings.warn("No negative samples in y_true, "


Wrapper: <__main__.HWrapperLazy object at 0x14c649550> not filled!


/Users/cerminar/.virtualenvs/HGCTPGPerformance-py3.8/lib/python3.8/site-packages/sklearn/metrics/_ranking.py:803: UndefinedMetricWarning: No negative samples in y_true, false positive value should be meaningless
  warnings.warn("No negative samples in y_true, "


Wrapper: <__main__.HWrapperLazy object at 0x14c62d3d0> not filled!


/Users/cerminar/.virtualenvs/HGCTPGPerformance-py3.8/lib/python3.8/site-packages/sklearn/metrics/_ranking.py:803: UndefinedMetricWarning: No negative samples in y_true, false positive value should be meaningless
  warnings.warn("No negative samples in y_true, "


Error in <THistPainter::PaintInit>: Cannot set Y axis to log scale
Error in <THistPainter::PaintInit>: Cannot set Y axis to log scale
Error in <THistPainter::PaintInit>: Cannot set Y axis to log scale
Error in <THistPainter::PaintInit>: Cannot set Y axis to log scale
Error in <THistPainter::PaintInit>: Cannot set Y axis to log scale
Error in <THistPainter::PaintInit>: Cannot set Y axis to log scale
Error in <THistPainter::PaintInit>: Cannot set Y axis to log scale
Error in <THistPainter::PaintInit>: Cannot set Y axis to log scale
Error in <THistPainter::PaintInit>: Cannot set Y axis to log scale
Error in <THistPainter::PaintInit>: Cannot set Y axis to log scale
Error in <THistPainter::PaintInit>: Cannot set Y axis to log scale
Error in <THistPainter::PaintInit>: Cannot set Y axis to log scale


In [75]:
hsets, labels, text = hplot_iso.get_histo(IsoPlot, ['dele'], 'PU200', ['tkEmEE'], ['EtaBCPt20Sig', 'EtaBCpPt20Sig', 'EtaBCmPt20Sig'], None)

draw([his.h_tkIso for his in hsets], labels, text=text,  
#      min_y=1, max_y=10000,
#      min_x=0, max_x=60,
     logy=True, 
     norm=True,
#      x_axis_label='online p_{T} thresh. [GeV]'
    )
draw([his.h_pfIso for his in hsets], labels, text=text,  
      min_y=1, max_y=10000,
#      min_x=0, max_x=60,
     logy=True, 
#      x_axis_label='online p_{T} thresh. [GeV]'
    )


Wrapper: <__main__.HWrapperLazy object at 0x14ceaa280> not filled!


/Users/cerminar/.virtualenvs/HGCTPGPerformance-py3.8/lib/python3.8/site-packages/sklearn/metrics/_ranking.py:803: UndefinedMetricWarning: No negative samples in y_true, false positive value should be meaningless
  warnings.warn("No negative samples in y_true, "


Wrapper: <__main__.HWrapperLazy object at 0x14c6492e0> not filled!


/Users/cerminar/.virtualenvs/HGCTPGPerformance-py3.8/lib/python3.8/site-packages/sklearn/metrics/_ranking.py:803: UndefinedMetricWarning: No negative samples in y_true, false positive value should be meaningless
  warnings.warn("No negative samples in y_true, "


Wrapper: <__main__.HWrapperLazy object at 0x14dd4edc0> not filled!


/Users/cerminar/.virtualenvs/HGCTPGPerformance-py3.8/lib/python3.8/site-packages/sklearn/metrics/_ranking.py:803: UndefinedMetricWarning: No negative samples in y_true, false positive value should be meaningless
  warnings.warn("No negative samples in y_true, "


Error in <THistPainter::PaintInit>: Cannot set Y axis to log scale
Error in <THistPainter::PaintInit>: Cannot set Y axis to log scale
Error in <THistPainter::PaintInit>: Cannot set Y axis to log scale
Error in <THistPainter::PaintInit>: Cannot set Y axis to log scale
Error in <THistPainter::PaintInit>: Cannot set Y axis to log scale
Error in <THistPainter::PaintInit>: Cannot set Y axis to log scale
Error in <THistPainter::PaintInit>: Cannot set Y axis to log scale
Error in <THistPainter::PaintInit>: Cannot set Y axis to log scale
Error in <THistPainter::PaintInit>: Cannot set Y axis to log scale
Error in <THistPainter::PaintInit>: Cannot set Y axis to log scale
Error in <THistPainter::PaintInit>: Cannot set Y axis to log scale
Error in <THistPainter::PaintInit>: Cannot set Y axis to log scale


In [76]:
hsets, labels, text = hplot_iso.get_histo(IsoPlot, ['dele'], 'PU200', ['tkEmEE'], ['EtaBCPt5Bkg', 'EtaBCpPt5Bkg', 'EtaBCmPt5Bkg'], None)

draw([his.h_tkIso for his in hsets], labels, text=text,  
#      min_y=1, max_y=10000,
#      min_x=0, max_x=60,
     logy=True, 
     norm=True,
#      x_axis_label='online p_{T} thresh. [GeV]'
    )
draw([his.h_pfIso for his in hsets], labels, text=text,  
      min_y=1, max_y=10000,
#      min_x=0, max_x=60,
     logy=True, 
#      x_axis_label='online p_{T} thresh. [GeV]'
    )


Wrapper: <__main__.HWrapperLazy object at 0x14de5d2b0> not filled!


/Users/cerminar/.virtualenvs/HGCTPGPerformance-py3.8/lib/python3.8/site-packages/sklearn/metrics/_ranking.py:811: UndefinedMetricWarning: No positive samples in y_true, true positive value should be meaningless
  warnings.warn("No positive samples in y_true, "


Wrapper: <__main__.HWrapperLazy object at 0x14c649730> not filled!


/Users/cerminar/.virtualenvs/HGCTPGPerformance-py3.8/lib/python3.8/site-packages/sklearn/metrics/_ranking.py:811: UndefinedMetricWarning: No positive samples in y_true, true positive value should be meaningless
  warnings.warn("No positive samples in y_true, "


Wrapper: <__main__.HWrapperLazy object at 0x14c62d1f0> not filled!


/Users/cerminar/.virtualenvs/HGCTPGPerformance-py3.8/lib/python3.8/site-packages/sklearn/metrics/_ranking.py:811: UndefinedMetricWarning: No positive samples in y_true, true positive value should be meaningless
  warnings.warn("No positive samples in y_true, "


Error in <THistPainter::PaintInit>: Cannot set Y axis to log scale
Error in <THistPainter::PaintInit>: Cannot set Y axis to log scale
Error in <THistPainter::PaintInit>: Cannot set Y axis to log scale
Error in <THistPainter::PaintInit>: Cannot set Y axis to log scale
Error in <THistPainter::PaintInit>: Cannot set Y axis to log scale
Error in <THistPainter::PaintInit>: Cannot set Y axis to log scale
Error in <THistPainter::PaintInit>: Cannot set Y axis to log scale
Error in <THistPainter::PaintInit>: Cannot set Y axis to log scale
Error in <THistPainter::PaintInit>: Cannot set Y axis to log scale
Error in <THistPainter::PaintInit>: Cannot set Y axis to log scale
Error in <THistPainter::PaintInit>: Cannot set Y axis to log scale
Error in <THistPainter::PaintInit>: Cannot set Y axis to log scale


In [ ]:
ROOT.gStyle.SetOptStat(True)


In [78]:
hsets, labels, text = hplot_iso.get_histo(IsoPlot, ['dpho'], 'PU200', ['PFTkEmEB'], ['EtaFPt10Sig'], None)

draw([his.h_tkIso for his in hsets], labels, text=text,  
     min_y=1, max_y=50000,
#      min_x=0, max_x=60,
     logy=True, 
#      x_axis_label='online p_{T} thresh. [GeV]'
    )
# draw([his.h_pfIso for his in hsets], labels, text=text,  
#       min_y=1, max_y=10000,
# #      min_x=0, max_x=60,
#      logy=True, 
# #      x_axis_label='online p_{T} thresh. [GeV]'
#     )
# draw([his.h_tkIsoPV for his in hsets], labels, text=text,  
#      min_y=1, max_y=10000,
# #      min_x=0, max_x=60,
#      logy=True, 
# #      x_axis_label='online p_{T} thresh. [GeV]'
#     )
# draw([his.h_pfIsoPV for his in hsets], labels, text=text,  
#       min_y=1, max_y=10000,
# #      min_x=0, max_x=60,
#      logy=True, 
# #      x_axis_label='online p_{T} thresh. [GeV]'
#     )


No match found for: sample: ['dpho'] pu: PU200, tp: ['PFTkEmEB'], tp_sel: ['EtaFPt10Sig'], gen_sel: None, classtype: <class '__main__.IsoPlot'>


TypeError: 'NoneType' object is not iterable

In [ ]:
hsets, labels, text = hplot_iso.get_histo(IsoPlot, ['dpho'], 'PU200', ['PFTkEmEE'], ['EtaABCPt10Sig'], None)

draw([his.h_tkIso for his in hsets], labels, text=text,  
     min_y=1, max_y=10000,
#      min_x=0, max_x=60,
     logy=True, 
#      x_axis_label='online p_{T} thresh. [GeV]'
    )
# draw([his.h_pfIso for his in hsets], labels, text=text,  
#       min_y=1, max_y=10000,
# #      min_x=0, max_x=60,
#      logy=True, 
# #      x_axis_label='online p_{T} thresh. [GeV]'
#     )
# draw([his.h_tkIsoPV for his in hsets], labels, text=text,  
#      min_y=1, max_y=10000,
# #      min_x=0, max_x=60,
#      logy=True, 
# #      x_axis_label='online p_{T} thresh. [GeV]'
#     )
# draw([his.h_pfIsoPV for his in hsets], labels, text=text,  
#       min_y=1, max_y=10000,
# #      min_x=0, max_x=60,
#      logy=True, 
# #      x_axis_label='online p_{T} thresh. [GeV]'
#     )


In [ ]:
hsets, labels, text = hplot_iso.get_histo(IsoPlot, ['dpho'], 'PU200', ['PFTkEmEE'], ['EtaABCPt10Bkg'], None)

draw([his.h_tkIso for his in hsets], labels, text=text,  
     min_y=1, max_y=10000,
#      min_x=0, max_x=60,
     logy=True, 
#      x_axis_label='online p_{T} thresh. [GeV]'
    )
# draw([his.h_pfIso for his in hsets], labels, text=text,  
#       min_y=1, max_y=10000,
# #      min_x=0, max_x=60,
#      logy=True, 
# #      x_axis_label='online p_{T} thresh. [GeV]'
#     )
# draw([his.h_tkIsoPV for his in hsets], labels, text=text,  
#      min_y=1, max_y=10000,
# #      min_x=0, max_x=60,
#      logy=True, 
# #      x_axis_label='online p_{T} thresh. [GeV]'
#     )
# draw([his.h_pfIsoPV for his in hsets], labels, text=text,  
#       min_y=1, max_y=10000,
# #      min_x=0, max_x=60,
#      logy=True, 
# #      x_axis_label='online p_{T} thresh. [GeV]'
#     )


In [79]:
hsets, labels, text = hplot_iso.get_histo(IsoPlot, ['dpho'], 'PU200', ['PFTkEmEE'], ['EtaBCPt10'], None)

draw([his.g_tkIso_effSig for his in hsets], labels, text=text,  
#     min_y=1, max_y=10000,
      min_x=0, max_x=1,
#      logy=True, 
#      x_axis_label='online p_{T} thresh. [GeV]'
    )
# draw([his.h_pfIso for his in hsets], labels, text=text,  
#       min_y=1, max_y=10000,
# #      min_x=0, max_x=60,
#      logy=True, 
# #      x_axis_label='online p_{T} thresh. [GeV]'
#     )
# draw([his.h_tkIsoPV for his in hsets], labels, text=text,  
#      min_y=1, max_y=10000,
# #      min_x=0, max_x=60,
#      logy=True, 
# #      x_axis_label='online p_{T} thresh. [GeV]'
#     )
# draw([his.h_pfIsoPV for his in hsets], labels, text=text,  
#       min_y=1, max_y=10000,
# #      min_x=0, max_x=60,
#      logy=True, 
# #      x_axis_label='online p_{T} thresh. [GeV]'
#     )


Wrapper: <__main__.HWrapperLazy object at 0x14de5fc10> not filled!


In [80]:
hsets, labels, text = hplot_iso.get_histo(IsoPlot, ['dpho'], 'PU200', ['PFTkEmEE'], ['EtaABCPt10'], None)

draw([his.g_tkIso_rejBkg for his in hsets], labels, text=text,  
#     min_y=1, max_y=10000,
      min_x=0, max_x=1,
#      logy=True, 
#      x_axis_label='online p_{T} thresh. [GeV]'
    )
# draw([his.h_pfIso for his in hsets], labels, text=text,  
#       min_y=1, max_y=10000,
# #      min_x=0, max_x=60,
#      logy=True, 
# #      x_axis_label='online p_{T} thresh. [GeV]'
#     )
# draw([his.h_tkIsoPV for his in hsets], labels, text=text,  
#      min_y=1, max_y=10000,
# #      min_x=0, max_x=60,
#      logy=True, 
# #      x_axis_label='online p_{T} thresh. [GeV]'
#     )
# draw([his.h_pfIsoPV for his in hsets], labels, text=text,  
#       min_y=1, max_y=10000,
# #      min_x=0, max_x=60,
#      logy=True, 
# #      x_axis_label='online p_{T} thresh. [GeV]'
#     )


No match found for: sample: ['dpho'] pu: PU200, tp: ['PFTkEmEE'], tp_sel: ['EtaABCPt10'], gen_sel: None, classtype: <class '__main__.IsoPlot'>


TypeError: 'NoneType' object is not iterable

In [81]:
hsets, labels, text = hplot_iso.get_histo(IsoPlot, ['dpho'], 'PU200', ['PFTkEmEE', 'tkEmEE'], ['EtaBCPt10'], None)

draw([his.g_tkIso_roc for his in hsets], labels, text=text,  
#     min_y=1, max_y=10000,
      min_x=0, max_x=1,
#      logy=True, 
#      x_axis_label='online p_{T} thresh. [GeV]'
    )
# draw([his.h_pfIso for his in hsets], labels, text=text,  
#       min_y=1, max_y=10000,
# #      min_x=0, max_x=60,
#      logy=True, 
# #      x_axis_label='online p_{T} thresh. [GeV]'
#     )
# draw([his.h_tkIsoPV for his in hsets], labels, text=text,  
#      min_y=1, max_y=10000,
# #      min_x=0, max_x=60,
#      logy=True, 
# #      x_axis_label='online p_{T} thresh. [GeV]'
#     )
# draw([his.h_pfIsoPV for his in hsets], labels, text=text,  
#       min_y=1, max_y=10000,
# #      min_x=0, max_x=60,
#      logy=True, 
# #      x_axis_label='online p_{T} thresh. [GeV]'
#     )


Wrapper: <__main__.HWrapperLazy object at 0x14cfb02e0> not filled!


In [90]:
hsets, labels, text = hplot_iso.get_histo(IsoPlot, ['dpho'], 'PU200', ['PFTkEmEE', 'tkEmEE'], ['EtaBCpPt10', 'EtaBCmPt10'], None)

draw([his.g_tkIso_roc for his in hsets], labels, text=text,  
#     min_y=1, max_y=10000,
      min_x=0, max_x=1,
#      logy=True, 
#      x_axis_label='online p_{T} thresh. [GeV]'
    )
# draw([his.h_pfIso for his in hsets], labels, text=text,  
#       min_y=1, max_y=10000,
# #      min_x=0, max_x=60,
#      logy=True, 
# #      x_axis_label='online p_{T} thresh. [GeV]'
#     )
# draw([his.h_tkIsoPV for his in hsets], labels, text=text,  
#      min_y=1, max_y=10000,
# #      min_x=0, max_x=60,
#      logy=True, 
# #      x_axis_label='online p_{T} thresh. [GeV]'
#     )
# draw([his.h_pfIsoPV for his in hsets], labels, text=text,  
#       min_y=1, max_y=10000,
# #      min_x=0, max_x=60,
#      logy=True, 
# #      x_axis_label='online p_{T} thresh. [GeV]'
#     )


In [83]:
hsets, labels, text = hplot_iso.get_histo(IsoPlot, ['dele'], 'PU200', ['PFTkEmEE', 'tkEmEE'], ['EtaBCpPt10', 'EtaBCmPt10'], None)

draw([his.g_tkIso_roc for his in hsets], labels, text=text,  
#     min_y=1, max_y=10000,
      min_x=0, max_x=1,
#      logy=True, 
#      x_axis_label='online p_{T} thresh. [GeV]'
    )
# draw([his.h_pfIso for his in hsets], labels, text=text,  
#       min_y=1, max_y=10000,
# #      min_x=0, max_x=60,
#      logy=True, 
# #      x_axis_label='online p_{T} thresh. [GeV]'
#     )
# draw([his.h_tkIsoPV for his in hsets], labels, text=text,  
#      min_y=1, max_y=10000,
# #      min_x=0, max_x=60,
#      logy=True, 
# #      x_axis_label='online p_{T} thresh. [GeV]'
#     )
# draw([his.h_pfIsoPV for his in hsets], labels, text=text,  
#       min_y=1, max_y=10000,
# #      min_x=0, max_x=60,
#      logy=True, 
# #      x_axis_label='online p_{T} thresh. [GeV]'
#     )


Wrapper: <__main__.HWrapperLazy object at 0x14c93ef40> not filled!
Wrapper: <__main__.HWrapperLazy object at 0x14d3f4a00> not filled!
Wrapper: <__main__.HWrapperLazy object at 0x14c649b50> not filled!
Wrapper: <__main__.HWrapperLazy object at 0x14c62d550> not filled!


In [84]:
hsets, labels, text = hplot_iso.get_histo(IsoPlot, ['dele'], 'PU200', ['PFTkEleEE', 'tkEleEE'], ['EtaBCpPt10', 'EtaBCmPt10'], None)

draw([his.g_tkIso_roc for his in hsets], labels, text=text,  
#     min_y=1, max_y=10000,
      min_x=0, max_x=1,
#      logy=True, 
#      x_axis_label='online p_{T} thresh. [GeV]'
    )
# draw([his.h_pfIso for his in hsets], labels, text=text,  
#       min_y=1, max_y=10000,
# #      min_x=0, max_x=60,
#      logy=True, 
# #      x_axis_label='online p_{T} thresh. [GeV]'
#     )
# draw([his.h_tkIsoPV for his in hsets], labels, text=text,  
#      min_y=1, max_y=10000,
# #      min_x=0, max_x=60,
#      logy=True, 
# #      x_axis_label='online p_{T} thresh. [GeV]'
#     )
# draw([his.h_pfIsoPV for his in hsets], labels, text=text,  
#       min_y=1, max_y=10000,
# #      min_x=0, max_x=60,
#      logy=True, 
# #      x_axis_label='online p_{T} thresh. [GeV]'
#     )


Wrapper: <__main__.HWrapperLazy object at 0x14dd61a00> not filled!
Wrapper: <__main__.HWrapperLazy object at 0x14d3c6d90> not filled!
Wrapper: <__main__.HWrapperLazy object at 0x14cf87880> not filled!
Wrapper: <__main__.HWrapperLazy object at 0x14c9d5a30> not filled!


In [ ]:
hsets, labels, text = hplot_iso.get_histo(IsoPlot, ['dpho'], 'PU200', ['PFTkEmEE'], ['EtaABCPt5Sig', 'EtaABCPt10Sig', 'EtaABCPt20Sig'], None)

draw([his.h_tkIso for his in hsets], labels, text=text,  
     min_y=1, max_y=10000,
#      min_x=0, max_x=60,
     logy=True, 
#      x_axis_label='online p_{T} thresh. [GeV]'
    )
draw([his.h_pfIso for his in hsets], labels, text=text,  
      min_y=1, max_y=10000,
#      min_x=0, max_x=60,
     logy=True, 
#      x_axis_label='online p_{T} thresh. [GeV]'
    )
draw([his.h_tkIsoPV for his in hsets], labels, text=text,  
     min_y=1, max_y=10000,
#      min_x=0, max_x=60,
     logy=True, 
#      x_axis_label='online p_{T} thresh. [GeV]'
    )
draw([his.h_pfIsoPV for his in hsets], labels, text=text,  
      min_y=1, max_y=10000,
#      min_x=0, max_x=60,
     logy=True, 
#      x_axis_label='online p_{T} thresh. [GeV]'
    )


In [ ]:
hsets, labels, text = hplot_iso.get_histo(IsoPlot, ['dele'], 'PU200', ['PFTkEleEE'], ['EtaABCPt5Bkg', 'EtaABCPt10Bkg', 'EtaABCPt20Bkg'], None)

draw([his.h_tkIso for his in hsets], labels, text=text,  
     min_y=1, max_y=10000,
#      min_x=0, max_x=60,
     logy=True, 
#      x_axis_label='online p_{T} thresh. [GeV]'
    )
draw([his.h_pfIso for his in hsets], labels, text=text,  
     min_y=1, max_y=10000,
#      min_x=0, max_x=60,
     logy=True, 
#      x_axis_label='online p_{T} thresh. [GeV]'
    )


In [85]:
hsets, labels, text = hplot_iso.get_histo(IsoPlot, ['dele'], 'PU200', ['PFTkEleEE', 'tkEleEE'], ['EtaBCpPt5', 'EtaBCmPt5'], None)

draw([his.g_tkIso_roc for his in hsets], labels, text=text,  
     min_y=0.85, max_y=1.05,
     h_lines=[1., 0.985]

#      min_x=0, max_x=60,
#      logy=True, x_axis_label='online p_{T} thresh. [GeV]'
    )
draw([his.g_tkIso_effSig for his in hsets], labels, text=text,  
     min_y=0.85, max_y=1.05,
     min_x=0, max_x=2,
     h_lines=[1., 0.985]
#      logy=True, x_axis_label='online p_{T} thresh. [GeV]'
    )

draw([his.g_tkIso_rejBkg for his in hsets], labels, text=text,  
     min_y=0.0, max_y=1.05,
     min_x=0, max_x=2,
     h_lines=[1., 0.985]
#      logy=True, x_axis_label='online p_{T} thresh. [GeV]'
    )


Wrapper: <__main__.HWrapperLazy object at 0x14dd61a90> not filled!
Wrapper: <__main__.HWrapperLazy object at 0x14d3c62e0> not filled!
Wrapper: <__main__.HWrapperLazy object at 0x14c90f880> not filled!
Wrapper: <__main__.HWrapperLazy object at 0x14c9d5160> not filled!


In [48]:
hsets, labels, text = hplot_iso.get_histo(IsoPlot, ['dele'], 'PU200', ['tkEleEE'], ['EtaBCpPt5', 'EtaBCmPt5'], None)

draw([his.g_tkIso_roc for his in hsets], labels, text=text,  
     min_y=0.85, max_y=1.05,
     h_lines=[1., 0.985]

#      min_x=0, max_x=60,
#      logy=True, x_axis_label='online p_{T} thresh. [GeV]'
    )
draw([his.g_tkIso_effSig for his in hsets], labels, text=text,  
     min_y=0.85, max_y=1.05,
     min_x=0, max_x=2,
     h_lines=[1., 0.985]
#      logy=True, x_axis_label='online p_{T} thresh. [GeV]'
    )

draw([his.g_tkIso_rejBkg for his in hsets], labels, text=text,  
     min_y=0.0, max_y=1.05,
     min_x=0, max_x=2,
     h_lines=[1., 0.985]
#      logy=True, x_axis_label='online p_{T} thresh. [GeV]'
    )


In [86]:
hsets, labels, text = hplot_iso.get_histo(IsoPlot, ['dpho'], 'PU200', ['PFTkEmEE'], ['EtaBCpPt5', 'EtaBCmPt5'], None)

draw([his.g_tkIso_roc for his in hsets], labels, text=text,  
     min_y=0.85, max_y=1.05,
     h_lines=[1., 0.985]

#      min_x=0, max_x=60,
#      logy=True, x_axis_label='online p_{T} thresh. [GeV]'
    )
draw([his.g_tkIso_effSig for his in hsets], labels, text=text,  
     min_y=0.85, max_y=1.05,
     min_x=0, max_x=2,
     h_lines=[1., 0.985]
#      logy=True, x_axis_label='online p_{T} thresh. [GeV]'
    )

draw([his.g_tkIso_rejBkg for his in hsets], labels, text=text,  
     min_y=0.5, max_y=0.85,
     min_x=0, max_x=2,
     h_lines=[1., 0.985]
#      logy=True, x_axis_label='online p_{T} thresh. [GeV]'
    )


Wrapper: <__main__.HWrapperLazy object at 0x14ce445b0> not filled!
Wrapper: <__main__.HWrapperLazy object at 0x14cfbcdc0> not filled!


In [92]:
hsets, labels, text = hplot_iso.get_histo(IsoPlot, ['dpho'], 'PU200', ['tkEmEE'], ['EtaBCpPt10', 'EtaBCmPt10'], None)

draw([his.g_tkIso_roc for his in hsets], labels, text=text,  
     min_y=0.1, max_y=1.05,
     h_lines=[1., 0.985]

#      min_x=0, max_x=60,
#      logy=True, x_axis_label='online p_{T} thresh. [GeV]'
    )
draw([his.g_tkIso_effSig for his in hsets], labels, text=text,  
     min_y=0.85, max_y=1.05,
     min_x=0, max_x=2,
     h_lines=[1., 0.985]
#      logy=True, x_axis_label='online p_{T} thresh. [GeV]'
    )

draw([his.g_tkIso_rejBkg for his in hsets], labels, text=text,  
     min_y=0.5, max_y=0.85,
     min_x=0, max_x=2,
     h_lines=[1., 0.985]
#      logy=True, x_axis_label='online p_{T} thresh. [GeV]'
    )


In [87]:
hsets, labels, text = hplot_iso.get_histo(IsoPlot, ['dpho'], 'PU200', ['tkEmEE'], ['EtaBCpPt5', 'EtaBCmPt5'], None)

draw([his.g_tkIso_roc for his in hsets], labels, text=text,  
     min_y=0.85, max_y=1.05,
     h_lines=[1., 0.985]

#      min_x=0, max_x=60,
#      logy=True, x_axis_label='online p_{T} thresh. [GeV]'
    )
draw([his.g_tkIso_effSig for his in hsets], labels, text=text,  
     min_y=0.85, max_y=1.05,
     min_x=0, max_x=2,
     h_lines=[1., 0.985]
#      logy=True, x_axis_label='online p_{T} thresh. [GeV]'
    )

draw([his.g_tkIso_rejBkg for his in hsets], labels, text=text,  
     min_y=0.5, max_y=0.85,
     min_x=0, max_x=2,
     h_lines=[1., 0.985]
#      logy=True, x_axis_label='online p_{T} thresh. [GeV]'
    )


Wrapper: <__main__.HWrapperLazy object at 0x14d82bc40> not filled!
Wrapper: <__main__.HWrapperLazy object at 0x14c264eb0> not filled!


In [100]:
hsets, labels, text = hplot_iso.get_histo(IsoPlot, ['dele'], 'PU200', ['tkEmEE', 'tkEleEE'], ['EtaBCpPt20', 'EtaBCmPt20'], None)

draw([his.g_tkIso_roc for his in hsets], labels, text=text,  
     min_y=0.85, max_y=1.05,
     h_lines=[1., 0.985]

#      min_x=0, max_x=60,
#      logy=True, x_axis_label='online p_{T} thresh. [GeV]'
    )
draw([his.g_tkIso_effSig for his in hsets], labels, text=text,  
     min_y=0.85, max_y=1.05,
     min_x=0, max_x=2,
     h_lines=[1., 0.985]
#      logy=True, x_axis_label='online p_{T} thresh. [GeV]'
    )

draw([his.g_tkIso_rejBkg for his in hsets], labels, text=text,  
     min_y=0.5, max_y=0.85,
     min_x=0, max_x=2,
     h_lines=[1., 0.985]
#      logy=True, x_axis_label='online p_{T} thresh. [GeV]'
    )


In [97]:
hsets, labels, text = hplot_iso.get_histo(IsoPlot, ['dele'], 'PU200', ['PFTkEmEE', 'PFTkEleEE'], ['EtaBCPt20'], None)

draw([his.g_tkIso_roc for his in hsets], labels, text=text,  
     min_y=0.85, max_y=1.05,
     h_lines=[1., 0.985]

#      min_x=0, max_x=60,
#      logy=True, x_axis_label='online p_{T} thresh. [GeV]'
    )
draw([his.g_tkIso_effSig for his in hsets], labels, text=text,  
     min_y=0.85, max_y=1.05,
     min_x=0, max_x=2,
     h_lines=[1., 0.985]
#      logy=True, x_axis_label='online p_{T} thresh. [GeV]'
    )

draw([his.g_tkIso_rejBkg for his in hsets], labels, text=text,  
     min_y=0.5, max_y=0.85,
     min_x=0, max_x=2,
     h_lines=[1., 0.985]
#      logy=True, x_axis_label='online p_{T} thresh. [GeV]'
    )


In [ ]:
hsets, labels, text = hplot_iso.get_histo(IsoPlot, ['dele'], 'PU200', ['PFTkEleEE'], ['EtaABCPt5', 'EtaABCPt10', 'EtaABCPt20', 'EtaABCPt25'], None)
draw([his.g_pfIso_roc for his in hsets], labels, text=text,  
     min_y=0.85, max_y=1.05,
     h_lines=[1., 0.985]

#      min_x=0, max_x=60,
#      logy=True, x_axis_label='online p_{T} thresh. [GeV]'
    )
draw([his.g_pfIso_effSig for his in hsets], labels, text=text,  
     min_y=0.85, max_y=1.05,
     min_x=0, max_x=2,
     h_lines=[1., 0.985]
#      logy=True, x_axis_label='online p_{T} thresh. [GeV]'
    )


In [ ]:
dm = DrawMachine(rleg_config)

hsets, labels, text = hplot_iso.get_histo(IsoPlot, ['dele'], 'PU200', ['PFTkEleEE'], ['EtaABCPt20'], None)
dm.addHistos([his.g_tkIso_roc for his in hsets], ['tkIso'])
# dm.addHistos([his.g_pt_online for his in hsets], ['online'])
# dm.addRatioHisto(1,0)
dm.addHistos([his.g_pfIso_roc for his in hsets], ['pfIso'])

dm.draw(
    text=text,
    y_min =0.85, y_max=1.05,
#     x_min=0, x_max=100,
#     y_log=True, x_axis_label='p_{T} thresh. [GeV]',
#     do_ratio=True,
#     options='hist'
    )



In [ ]:
import ctypes

iso_wps_obj = {}

def get_wpsCuts(graph, label, wps):
    res = {}
    res_wps = {}
    for wp in wps:
        for ib in range(0,graph.GetN()):
            x = ctypes.c_double(0.)
            y = ctypes.c_double(0.)
            graph.GetPoint(ib, x, y)
#             print(f'{ib}: x: {x.value} y: {y.value}')
            if y.value < wp:
                graph.GetPoint(ib-1, x, y)
                print(f'{text}, {label}, WP: {wp}, iso cut: {x.value:.2f}')
                res_wps[wp] = round(x.value, 2)
                break
    res[label] = res_wps
    return res

In [ ]:
iso_wps = {
    'tkIso': {},
    'tkIsoPV': {},
    'pfIso': {},
    'pfIsoPV': {}}

for sel in ['EtaFPt10', 'EtaFPt20', 'EtaFPt40']:
    hsets, labels, text = hplot_iso.get_histo(IsoPlot, ['dpho'], 'PU200', ['PFTkEmEB'], sel, None)
    for hi,his in enumerate(hsets):
        iso_wps['tkIso'].update(get_wpsCuts(graph=his.g_tkIso_effSig, label=sel, wps=[0.95, 0.98]))
        iso_wps['tkIsoPV'].update(get_wpsCuts(graph=his.g_tkIsoPV_effSig, label=sel, wps=[0.95, 0.98]))
        iso_wps['pfIso'].update(get_wpsCuts(graph=his.g_pfIso_effSig, label=sel, wps=[0.95, 0.98]))
        iso_wps['pfIsoPV'].update(get_wpsCuts(graph=his.g_pfIsoPV_effSig, label=sel, wps=[0.95, 0.98]))

iso_wps_obj['PFTkEmEB'] = iso_wps
    
    
pp.pprint(iso_wps_obj)
    

In [ ]:
iso_wps = {
    'tkIso': {},
    'tkIsoPV': {},
    'pfIso': {},
    'pfIsoPV': {}}

for sel in ['EtaABCPt10', 'EtaABCPt20', 'EtaABCPt40']:
    hsets, labels, text = hplot_iso.get_histo(IsoPlot, ['dpho'], 'PU200', ['PFTkEmEE'], sel, None)
    for hi,his in enumerate(hsets):
        iso_wps['tkIso'].update(get_wpsCuts(graph=his.g_tkIso_effSig, label=sel, wps=[0.95, 0.98]))
        iso_wps['tkIsoPV'].update(get_wpsCuts(graph=his.g_tkIsoPV_effSig, label=sel, wps=[0.95, 0.98]))
        iso_wps['pfIso'].update(get_wpsCuts(graph=his.g_pfIso_effSig, label=sel, wps=[0.95, 0.98]))
        iso_wps['pfIsoPV'].update(get_wpsCuts(graph=his.g_pfIsoPV_effSig, label=sel, wps=[0.95, 0.98]))

iso_wps_obj['PFTkEmEE'] = iso_wps
    
    
    

In [ ]:
import json
pp.pprint(iso_wps_obj)
with open('iso_wps.json', 'w') as fp:
    json.dump(iso_wps_obj, fp)

In [ ]:
import tabulate

In [ ]:
table = []
wp = 0.98
tp_wp = iso_wps_obj['PFTkEmEB']
headers = tp_wp.keys()
for pt in [10, 20, 25, 40]:
    row = []
    row.append(f'pT > {pt}GeV')
    for head in headers:
        row.append(tp_wp[head][f'EtaFPt{pt}'][wp])
    table.append(row)
    
print(tabulate.tabulate(table, headers=[f'WP@{wp}%']+list(headers)))

In [ ]:
table = []
wp = 0.95
tp_wp = iso_wps_obj['PFTkEmEB']
headers = tp_wp.keys()
for pt in [10, 20, 25, 40]:
    row = []
    row.append(f'pT > {pt}GeV')
    for head in headers:
        row.append(tp_wp[head][f'EtaFPt{pt}'][wp])
    table.append(row)
    
print(tabulate.tabulate(table, headers=[f'WP@{wp}%']+list(headers)))

In [ ]:
table = []
wp = 0.95
tp_wp = iso_wps_obj['PFTkEmEE']
headers = tp_wp.keys()
for pt in [10, 20, 25, 40]:
    row = []
    row.append(f'pT > {pt}GeV')
    for head in headers:
        row.append(tp_wp[head][f'EtaABCPt{pt}'][wp])
    table.append(row)
    
print(tabulate.tabulate(table, headers=[f'WP@{wp}%']+list(headers)))

In [ ]:
table = []
wp = 0.98
tp_wp = iso_wps_obj['PFTkEmEE']
headers = tp_wp.keys()
for pt in [10, 20, 25, 40]:
    row = []
    row.append(f'pT > {pt}GeV')
    for head in headers:
        row.append(tp_wp[head][f'EtaABCPt{pt}'][wp])
    table.append(row)
    
print(tabulate.tabulate(table, headers=[f'WP@{wp}%']+list(headers)))

In [ ]:

hsets, labels, text = hplot_iso.get_histo(
    IsoPlot, 
    ['dpho'], 
    'PU200', 
    ['PFTkEmEB'], 
    ['EtaFPt10', 'EtaFPt20',  'EtaFPt25', 'EtaFPt40',
#     'EtaFGENPt10', 'EtaFGENPt20',  'EtaFGENPt25', 'EtaFGENPt40',
    ], 
    None)
# dm.addHistos([his.g_pt_online for his in hsets], ['online'])
# dm.addRatioHisto(1,0)
# dm.addHistos([his.g_pfIso_roc for his in hsets],la)

dm = DrawMachine(rleg_config)
dm.addHistos([his.g_tkIso_effSig for his in hsets], labels)
dm.draw(text=text, 
        y_min =0.85, y_max=1.05,
        x_min=0, x_max=1,
        h_lines=[1., 0.98, 0.95])

dm = DrawMachine(rleg_config)
dm.addHistos([his.g_tkIsoPV_effSig for his in hsets], labels)
dm.draw(
    text=text,
    y_min =0.85, y_max=1.05,
    x_min=0, x_max=1,
    h_lines=[1., 0.98, 0.95]
#     y_log=True, x_axis_label='p_{T} thresh. [GeV]',
#     do_ratio=True,
#     options='hist'
    )

dm = DrawMachine(rleg_config)
dm.addHistos([his.g_pfIso_effSig for his in hsets], labels)
dm.draw(
    text=text,
    y_min =0.85, y_max=1.05,
    x_min=0, x_max=2,
    h_lines=[1., 0.98, 0.95]
#     y_log=True, x_axis_label='p_{T} thresh. [GeV]',
#     do_ratio=True,
#     options='hist'
    )

dm = DrawMachine(rleg_config)
dm.addHistos([his.g_pfIsoPV_effSig for his in hsets], labels)
dm.draw(
    text=text,
    y_min =0.85, y_max=1.05,
    x_min=0, x_max=2,
    h_lines=[1., 0.98, 0.95]
#     y_log=True, x_axis_label='p_{T} thresh. [GeV]',
#     do_ratio=True,
#     options='hist'
    )


In [ ]:
import ctypes

hsets, labels, text = hplot_iso.get_histo(
    IsoPlot, 
    ['dpho'], 
    'PU200', 
    ['PFTkEmEE'], 
    ['EtaABCPt10', 'EtaABCPt20',  'EtaABCPt25',  'EtaABCPt40', 
#      'EtaABCGENPt10', 'EtaABCGENPt20',  'EtaABCGENPt25',  'EtaABCGENPt40'
    ], 
    None)


dm = DrawMachine(rleg_config)
dm.addHistos([his.g_tkIso_effSig for his in hsets], labels)
dm.draw(text=text,
        y_min =0.85, y_max=1.05,
        x_min=0, x_max=1,
        h_lines=[1., 0.98, 0.95])

dm = DrawMachine(rleg_config)
dm.addHistos([his.g_tkIsoPV_effSig for his in hsets], labels)
dm.draw(
    text=text,
    y_min =0.85, y_max=1.05,
    x_min=0, x_max=1,
    h_lines=[1., 0.98, 0.95]
#     y_log=True, x_axis_label='p_{T} thresh. [GeV]',
#     do_ratio=True,
#     options='hist'
    )

dm = DrawMachine(rleg_config)
dm.addHistos([his.g_pfIso_effSig for his in hsets], labels)
dm.draw(
    text=text,
    y_min =0.85, y_max=1.05,
    x_min=0, x_max=1,
    h_lines=[1., 0.98, 0.95]
#     y_log=True, x_axis_label='p_{T} thresh. [GeV]',
#     do_ratio=True,
#     options='hist'
    )

dm = DrawMachine(rleg_config)
dm.addHistos([his.g_pfIsoPV_effSig for his in hsets], labels)
dm.draw(
    text=text,
    y_min =0.85, y_max=1.05,
    x_min=0, x_max=1,
    h_lines=[1., 0.98, 0.95]
#     y_log=True, x_axis_label='p_{T} thresh. [GeV]',
#     do_ratio=True,
#     options='hist'
    )


In [ ]:
dm = DrawMachine(rleg_config)

hsets, labels, text = hplot_iso.get_histo(IsoPlot, ['dpho'], 'PU200', ['PFTkEmEE'], ['EtaABCPt10'], None)
dm.addHistos([his.g_tkIso_roc for his in hsets], ['tkIso'])
# dm.addHistos([his.g_pt_online for his in hsets], ['online'])
# dm.addRatioHisto(1,0)
dm.addHistos([his.g_pfIso_roc for his in hsets], ['pfIso'])

dm.draw(
    text=text,
    y_min =0.85, y_max=1.05,
#     x_min=0, x_max=100,
#     y_log=True, x_axis_label='p_{T} thresh. [GeV]',
#     do_ratio=True,
#     options='hist'
    )



In [ ]:
dm = DrawMachine(rleg_config)

hsets, labels, text = hplot_iso.get_histo(IsoPlot, ['dpho'], 'PU200', ['PFTkEmEB'], ['EtaFPt10'], None)
dm.addHistos([his.g_tkIsoPV_effSig for his in hsets], ['tkIsoPV'])
dm.addHistos([his.g_pfIsoPV_effSig for his in hsets], ['pfIsoPV'])
dm.addHistos([his.g_tkIso_effSig for his in hsets], ['tkIso'])
dm.addHistos([his.g_pfIso_effSig for his in hsets], ['pfIso'])

dm.draw(
    text=text,
    y_min =0.85, y_max=1.05,
    x_min=0, x_max=3,
#     y_log=True, x_axis_label='p_{T} thresh. [GeV]',
#     do_ratio=True,
#     options='hist'
    h_lines=[1., 0.98]
    )



In [ ]:
dm = DrawMachine(rleg_config)

hsets, labels, text = hplot_iso.get_histo(IsoPlot, ['dpho'], 'PU200', ['PFTkEmEB'], ['EtaFPt10'], None)
dm.addHistos([his.g_tkIsoPV_rejBkg for his in hsets], ['tkIsoPV'])
dm.addHistos([his.g_pfIsoPV_rejBkg for his in hsets], ['pfIsoPV'])
dm.addHistos([his.g_tkIso_rejBkg for his in hsets], ['tkIso'])
dm.addHistos([his.g_pfIso_rejBkg for his in hsets], ['pfIso'])

dm.draw(
    text=text,
    y_min =0.2, y_max=1.05,
    x_min=0, x_max=1,
#     y_log=True, x_axis_label='p_{T} thresh. [GeV]',
#     do_ratio=True,
#     options='hist'
    h_lines=[1., 0.98]
    )



In [ ]:
dm = DrawMachine(rleg_config)

hsets, labels, text = hplot_iso.get_histo(IsoPlot, ['dpho'], 'PU200', ['PFTkEmEB'], ['EtaFPt20'], None)
dm.addHistos([his.g_tkIsoPV_rejBkg for his in hsets], ['tkIsoPV'])
dm.addHistos([his.g_pfIsoPV_rejBkg for his in hsets], ['pfIsoPV'])
dm.addHistos([his.g_tkIso_rejBkg for his in hsets], ['tkIso'])
dm.addHistos([his.g_pfIso_rejBkg for his in hsets], ['pfIso'])

dm.draw(
    text=text,
    y_min =0.2, y_max=1.05,
    x_min=0, x_max=1,
#     y_log=True, x_axis_label='p_{T} thresh. [GeV]',
#     do_ratio=True,
#     options='hist'
    h_lines=[1., 0.98]
    )



In [ ]:
dm = DrawMachine(rleg_config)

hsets, labels, text = hplot_iso.get_histo(IsoPlot, ['dpho'], 'PU200', ['PFTkEmEB'], ['EtaFPt10'], None)
dm.addHistos([his.g_tkIsoPV_roc for his in hsets], ['tkIsoPV'])
dm.addHistos([his.g_pfIsoPV_roc for his in hsets], ['pfIsoPV'])
dm.addHistos([his.g_tkIso_roc for his in hsets], ['tkIso'])
dm.addHistos([his.g_pfIso_roc for his in hsets], ['pfIso'])

dm.draw(
    text=text,
    y_min =0.2, y_max=1.05,
    x_min=0, x_max=1,
#     y_log=True, x_axis_label='p_{T} thresh. [GeV]',
#     do_ratio=True,
#     options='hist'
    h_lines=[1., 0.98]
    )



In [ ]:
dm = DrawMachine(rleg_config)

hsets, labels, text = hplot_iso.get_histo(IsoPlot, ['dpho'], 'PU200', ['PFTkEmEB'], ['EtaFPt20'], None)
dm.addHistos([his.g_tkIsoPV_roc for his in hsets], ['tkIsoPV'])
dm.addHistos([his.g_pfIsoPV_roc for his in hsets], ['pfIsoPV'])
dm.addHistos([his.g_tkIso_roc for his in hsets], ['tkIso'])
dm.addHistos([his.g_pfIso_roc for his in hsets], ['pfIso'])

dm.draw(
    text=text,
    y_min =0.2, y_max=1.05,
    x_min=0, x_max=1,
#     y_log=True, x_axis_label='p_{T} thresh. [GeV]',
#     do_ratio=True,
#     options='hist'
    h_lines=[1., 0.98]
    )



In [ ]:
dm = DrawMachine(rleg_config)

hsets, labels, text = hplot_iso.get_histo(IsoPlot, ['dpho'], 'PU200', ['PFTkEmEE'], ['EtaABCPt10'], None)
dm.addHistos([his.g_tkIsoPV_effSig for his in hsets], ['tkIsoPV'])
dm.addHistos([his.g_pfIsoPV_effSig for his in hsets], ['pfIsoPV'])
dm.addHistos([his.g_tkIso_effSig for his in hsets], ['tkIso'])
dm.addHistos([his.g_pfIso_effSig for his in hsets], ['pfIso'])

dm.draw(
    text=text,
    y_min =0.85, y_max=1.05,
    x_min=0, x_max=1,
#     y_log=True, x_axis_label='p_{T} thresh. [GeV]',
#     do_ratio=True,
#     options='hist'
    h_lines=[1., 0.98]
    )



In [ ]:
dm = DrawMachine(rleg_config)

hsets, labels, text = hplot_iso.get_histo(IsoPlot, ['dpho'], 'PU200', ['PFTkEmEE'], ['EtaABCPt20'], None)
dm.addHistos([his.g_tkIsoPV_effSig for his in hsets], ['tkIsoPV'])
dm.addHistos([his.g_pfIsoPV_effSig for his in hsets], ['pfIsoPV'])
dm.addHistos([his.g_tkIso_effSig for his in hsets], ['tkIso'])
dm.addHistos([his.g_pfIso_effSig for his in hsets], ['pfIso'])

dm.draw(
    text=text,
    y_min =0.85, y_max=1.05,
    x_min=0, x_max=1,
#     y_log=True, x_axis_label='p_{T} thresh. [GeV]',
#     do_ratio=True,
#     options='hist'
    h_lines=[1., 0.98]
    )



In [ ]:
dm = DrawMachine(rleg_config)

hsets, labels, text = hplot_iso.get_histo(IsoPlot, ['dpho'], 'PU200', ['PFTkEmEE'], ['EtaBCPt10'], None)
dm.addHistos([his.g_tkIsoPV_rejBkg for his in hsets], ['tkIsoPV'])
# dm.addHistos([his.g_pt_online for his in hsets], ['online'])
# dm.addRatioHisto(1,0)
dm.addHistos([his.g_pfIsoPV_rejBkg for his in hsets], ['pfIsoPV'])
dm.addHistos([his.g_tkIso_rejBkg for his in hsets], ['tkIso'])
# dm.addHistos([his.g_pt_online for his in hsets], ['online'])
# dm.addRatioHisto(1,0)
dm.addHistos([his.g_pfIso_rejBkg for his in hsets], ['pfIso'])

dm.draw(
    text=text,
#     y_min =0.85, y_max=1.05,
    x_min=0, x_max=1,
#     y_log=True, x_axis_label='p_{T} thresh. [GeV]',
#     do_ratio=True,
#     options='hist'
    h_lines=[1., 0.98]
    )



In [ ]:
dm = DrawMachine(rleg_config)

hsets, labels, text = hplot_iso.get_histo(IsoPlot, ['dpho'], 'PU200', ['PFTkEmEE'], ['EtaABCPt10'], None)
dm.addHistos([his.g_tkIsoPV_roc for his in hsets], ['tkIsoPV'])
# dm.addHistos([his.g_pt_online for his in hsets], ['online'])
# dm.addRatioHisto(1,0)
dm.addHistos([his.g_pfIsoPV_roc for his in hsets], ['pfIsoPV'])
dm.addHistos([his.g_tkIso_roc for his in hsets], ['tkIso'])
# dm.addHistos([his.g_pt_online for his in hsets], ['online'])
# dm.addRatioHisto(1,0)
dm.addHistos([his.g_pfIso_roc for his in hsets], ['pfIso'])

dm.draw(
    text=text,
    y_min =0.85, y_max=1.05,
#     x_min=0, x_max=100,
#     y_log=True, x_axis_label='p_{T} thresh. [GeV]',
#     do_ratio=True,
#     options='hist'
    h_lines=[1., 0.98]
    )



In [ ]:
dm = DrawMachine(rleg_config)

hsets, labels, text = hplot_iso.get_histo(IsoPlot, ['dpho'], 'PU200', ['PFTkEmEE'], ['EtaABCPt5'], None)
dm.addHistos([his.g_tkIsoPV_roc for his in hsets], ['tkIsoPV'])
# dm.addHistos([his.g_pt_online for his in hsets], ['online'])
# dm.addRatioHisto(1,0)
# dm.addHistos([his.g_pfIsoPV_roc for his in hsets], ['pfIsoPV'])
dm.addHistos([his.g_tkIso_roc for his in hsets], ['tkIso'])
# dm.addHistos([his.g_pt_online for his in hsets], ['online'])
# dm.addRatioHisto(1,0)
# dm.addHistos([his.g_pfIso_roc for his in hsets], ['pfIso'])

dm.draw(
    text=text,
    y_min =0.85, y_max=1.05,
#     x_min=0, x_max=100,
#     y_log=True, x_axis_label='p_{T} thresh. [GeV]',
#     do_ratio=True,
#     options='hist'
    )



In [ ]:
dm = DrawMachine(rleg_config)

hsets, labels, text = hplot_iso.get_histo(IsoPlot, ['dpho'], 'PU200', ['PFTkEmEE'], ['EtaABCPt5'], None)
dm.addHistos([his.g_tkIsoPV_effSig for his in hsets], ['tkIsoPV'])
# dm.addHistos([his.g_pt_online for his in hsets], ['online'])
# dm.addRatioHisto(1,0)
dm.addHistos([his.g_pfIsoPV_effSig for his in hsets], ['pfIsoPV'])
dm.addHistos([his.g_tkIso_effSig for his in hsets], ['tkIso'])
# dm.addHistos([his.g_pt_online for his in hsets], ['online'])
# dm.addRatioHisto(1,0)
dm.addHistos([his.g_pfIso_effSig for his in hsets], ['pfIso'])

dm.draw(
    text=text,
    y_min =0.85, y_max=1.05,
#     x_min=0, x_max=100,
#     y_log=True, x_axis_label='p_{T} thresh. [GeV]',
#     do_ratio=True,
#     options='hist'
    )



In [ ]:
dm = DrawMachine(rleg_config)

hsets, labels, text = hplot_iso.get_histo(IsoPlot, ['dele'], 'PU200', ['PFTkEleEE'], ['EtaBCPt20'], None)
dm.addHistos([his.g_tkIso_roc for his in hsets], ['tkIso'])
# dm.addHistos([his.g_pt_online for his in hsets], ['online'])
# dm.addRatioHisto(1,0)
dm.addHistos([his.g_pfIso_roc for his in hsets], ['pfIso'])

dm.draw(
    text=text,
    y_min =0.85, y_max=1.05,
#     x_min=0, x_max=100,
#     y_log=True, x_axis_label='p_{T} thresh. [GeV]',
#     do_ratio=True,
#     options='hist'
    )



In [ ]:
print (len(fpr), len(tpr), len(thresholds))
print (type(fpr), type(tpr), type(thresholds))


In [ ]:
graph = ROOT.TGraph(len(fpr), fpr, 1-tpr)

In [ ]:
draw(histograms=[graph],
     labels=['iso'])

In [ ]:
graph = ROOT.TGraph(len(thresholds), array.array('d', thresholds), 1-tpr)

In [ ]:
draw(histograms=[graph],
     labels=['iso'])

In [ ]:
plt.figure()
lw = 2
plt.plot(fpr, tpr, color='darkorange',
         lw=lw, label='ROC curve (area = %0.2f)' % roc_auc[2])
plt.plot([0, 1], [0, 1], color='navy', lw=lw, linestyle='--')
plt.xlim([0.0, 1.0])
plt.ylim([0.0, 1.05])
plt.xlabel('False Positive Rate')
plt.ylabel('True Positive Rate')
plt.title('Receiver operating characteristic example')
plt.legend(loc="lower right")
plt.show()